In [1]:
import csv
import pandas as pd
pd.options.display.max_rows = None
pd.options.display.max_columns = None
import datetime 
from dateutil.relativedelta import relativedelta
import requests
import time
import re
from bs4 import BeautifulSoup

In [2]:
HEADERS = {'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/105.0.0.0 Safari/537.36 Edg/106.0.1370.42'}
initial_URL = "https://www.propertyfinder.eg/en/search?c=1&ob=nd&page=1&pf=1&pt=3000000"
URL = initial_URL
base_url = "https://www.propertyfinder.eg/en/search?c=1&ob=nd&page="
url_tail = "&pf=1&pt=3000000"


In [4]:
def get_soup(URL):
    page_response = requests.get(URL,headers=HEADERS)
    #print(page_response.url)
    soup = BeautifulSoup(page_response.content, "html.parser")
    return soup
    #print(soup.prettify())

In [5]:
def increment_page(counter):
    URL = f"{base_url}{str(counter + 1)}{url_tail}"
    return URL
    

In [6]:
def get_past_date(str_days_ago): #code I found online to convert x days ago to listing date
    TODAY = datetime.date.today()
    splitted = str_days_ago.split()
    if len(splitted) == 1 and splitted[0].lower() == 'today':
        return str(TODAY.isoformat())
    elif len(splitted) == 1 and splitted[0].lower() == 'yesterday':
        date = TODAY - relativedelta(days=1)
        return str(date.isoformat())
    elif splitted[1].lower() in ['minutes', 'minute', 'min']:
        date = datetime.datetime.now() - relativedelta(minutes=int(splitted[0]))
        return str(date.date().isoformat())
    elif splitted[1].lower() in ['hour', 'hours', 'hr', 'hrs', 'h']:
        date = datetime.datetime.now() - relativedelta(hours=int(splitted[0]))
        return str(date.date().isoformat())
    elif splitted[1].lower() in ['day', 'days', 'd']:
        date = TODAY - relativedelta(days=int(splitted[0]))
        return str(date.isoformat())
    elif splitted[1].lower() in ['wk', 'wks', 'week', 'weeks', 'w']:
        date = TODAY - relativedelta(weeks=int(splitted[0]))
        return str(date.isoformat())
    elif splitted[1].lower() in ['mon', 'mons', 'month', 'months', 'm']:
        date = TODAY - relativedelta(months=int(splitted[0]))
        return str(date.isoformat())
    elif splitted[1].lower() in ['yrs', 'yr', 'years', 'year', 'y']:
        date = TODAY - relativedelta(years=int(splitted[0]))
        return str(date.isoformat())
    else:
        return "Wrong Argument format"
    


In [7]:
#function that doesn't allow duplicates in the csv file
def csv_exist(facts_list, file):
    pk = facts_list[0]
    file_reader = csv.reader(file)
    for line in file_reader:
        if line[0] == pk:
            return True;
            break;
    return False;



In [8]:
def price_exists(div): #returns false if property price is not specified
    p = div.find("p", {"class": "card-intro__price"}).text
    pattern = re.compile(r'\bEGP\b')
    if(len(re.findall(pattern, p)) == 0):
        return False
    else :
        return True

In [9]:
properties_facts = [["null", "null", "null", "null", "null", "null", "null", "null", "null", "null", "null"]]
amenities_facts = [["null", "null"]]
listing_agents_facts = [["null", "null", "null"]]
broker_companies_facts = [["null", "null", "null", "null"]]
dev_projects_facts = [["null", "null"]] 

In [10]:
def clear_dataframes(lst1,lst2,lst3,lst4,lst5):
    lst1.clear()
    lst2.clear()
    lst3.clear()
    lst4.clear()
    lst5.clear()
    lst1.append(["null", "null", "null", "null", "null", "null", "null", "null", "null", "null", "null"])
    lst2.append(["null", "null"])
    lst3.append(["null", "null", "null"])
    lst4.append(["null", "null", "null", "null"])
    lst5.append(["null", "null"])
    

In [11]:
def update_df(df, x_facts):
    df = df.append(pd.DataFrame(x_facts))
    df = df.drop_duplicates()
    

In [126]:
#devprojects_df.drop(devprojects_df.index,inplace=True)
devprojects_df = pd.DataFrame(dev_projects_facts)
devprojects_df.columns = ['Project Name', 'Project Location']
devprojects_df = devprojects_df.drop_duplicates()
devprojects_df
#devprojects_df.to_csv(r'D:\property_finder_db\Development_projects - Sheet1.csv')

Project Name                                Project Location
0                   null                                            null
1   La Verde New Capital  Cairo, New Capital City, New Capital Compounds
2                Rivan**  Cairo, New Capital City, New Capital Compounds
4                 Rhodes  Cairo, New Capital City, New Capital Compounds
9          Isola October           Giza, 6 October City, Hadayek October
11  La Verde New Capital                         Cairo, New Capital City

In [107]:
#amenities_df.drop(amenities_df.index,inplace=True)
amenities_df = pd.DataFrame(amenities_facts)
amenities_df.columns = [ 'Reference Number','amenity description']
amenities_df = amenities_df.drop_duplicates()
amenities_df
amenities_df.to_csv(r'D:\property_finder_db\amenities - Sheet1.csv')

In [108]:
#agents_df.drop(agents_df.index,inplace=True)
agents_df = pd.DataFrame(listing_agents_facts)
agents_df.columns = ['Listing agent phone number', 'Agent name', 'Broker company phone number']
agents_df = agents_df.drop_duplicates()
agents_df
agents_df.to_csv(r'D:\property_finder_db\Listing_agents - Sheet1.csv')

In [144]:
#broker_df.drop(broker_df.index,inplace=True)
broker_df = pd.DataFrame(broker_companies_facts)
broker_df.columns = ['Broker Phone Number', 'Broker Company Name', 'Company Address', 'Number of listed properties']
broker_df = broker_df.drop_duplicates()

for ind in broker_df.index:
    corrupted_address = broker_df.at[ind,'Company Address']
    corrupted_address = corrupted_address.replace('\n', '')
    corrupted_address = corrupted_address.replace(',', '')
    corrupted_address = corrupted_address.replace('،', '')
    
    print(corrupted_address)
    broker_df.at[ind,'Company Address'] = corrupted_address
broker_df.drop(['Company Address'], axis = 1, inplace = True)
broker_df.to_csv(r'D:\property_finder_db\Broker_companies - Sheet1.csv')
broker_df

null
"16 Nasr Ahmed Zaki From elbatrawy street Cairo. Egypt"
"238 El- Geish road Arous el ba7r builduing roushdy "
"فيلا ٢١ شارع اخناتون - الحي الخامس - التجمع الخامس"
"122 District 3 /4 Fifth Settlement Cairo Egypt "
القاهرة "
"Banafseg mall 7  new cairo "
القليوبية"
"NEW CAIRO"
"In front of The spot Mall Building 105 "
"3 عبد الرحمن الرافعي  الدور السادس المهندسين"
"ggg"
"Waterway "
الدور الارضي شقة ٢"
"١٧٨ طريق الحريه الابراهيميه "
" النيل الأبيض متفرع من ميدان لبنان المهندسين 8 "
"Heliopolis"
"Cotton towers Alexandria  Egypt  "
"Villa 210  Elshwfat  new cairo "
"المعادي الجديده "
" ٨٤ ع  حي اول مجاورة ثالثة - امام مدرسة نجيب محفوظ"
"30  Sheikh Zayed City 7th District Giza Egypt"
"new cairo"
"nasr city"
"VILLA 57 STREET 90 new cairo"
"18 Mahmoud Eldeeb Intersection with Adly yakn Gleem Alexandria Alexandria Governorate Egypt 21615"
"شارع السلولي -الدقي ١٣ "
"سما مول الحي الثاني المنطقة الاولي  التجمع الخامس الدور ٣"
"new cairo"
" ٢١ ش الخليفه المامون روكسى - مصر الجديده - الدور الخا

Broker Phone Number  \
0                          null   
1                 +201064247555   
2                 +201000552273   
3                 +201111048006   
4                 +201092892866   
5                 +201009366996   
6                 +201116759157   
7                 +201050404653   
8                 +201010591385   
9                 +201120523333   
10                +201111199110   
11                +201064333222   
12                +201234555575   
13                +201050863940   
14                +201023401272   
15                +201140004084   
19                +201061144201   
20                +201022214789   
21                +201026960166   
26                +201001483076   
28                +201091956669   
29                +201155468540   
32                +201555550266   
33                +201228032707   
34                +201225151797   
37                +201063035246   
40                +201113377778   
49                +201061951911   
52                +201555550266   
56                +201004353926   
61                +201201111720   
62                +201115171110   
63                +201121190144   
66                +201149679050   
70                +201013615156   
72                +201060172517   
73                +201063000473   
77                +201001483076   
81                +201126114730   
84                +201110708383   
87                +201100888203   
95                +201006816398   
98                +201207233761   
100               +201006667804   
105               +201111120541   
108               +201120331170   
109               +201009104100   
113               +201030002538   
114               +201006102105   
116               +201000057258   
117               +201001483076   
119               +201008881386   
120               +201023240179   
123               +201020273707   
126               +201002620836   
128               +201016611000   
130               +201022614123   
132               +201119333913   
134               +201099222621   
135               +201118985559   
136               +201122655561   
137               +201141066622   
138               +201002099549   
143               +201060484017   
144                +20109444901   
152               +201015514400   
153               +201050774474   
154               +201008502001   
159               +201095354446   
160               +201000048249   
161               +201116555699   
163               +201024084027   
168               +201121111535   
178               +201226204656   
182               +201284440141   
192               +201159058050   
200               +201281277170   
202               +201223954594   
212               +201003922929   
216               +201222582885   
218               +201096061009   
220               +201016164162   
222               +201001399310   
227               +201201763620   
232               +201066913334   
234               +201012223375   
240               +201011157667   
241               +201289225412   
242               +201112388480   
246               +201274850000   
247               +201113345494   
248               +201009960944   
250               +201007111169   
251               +201094001166   
252               +201091037544   
254               +201288182682   
257               +201140433702   
258               +201000052576   
264               +201110248881   
267               +201020844778   
269               +201118321817   
278               +201032977977   
292               +201140004007   
294               +201156664901   
295               +201119991466   
297               +201211243500   
298               +201093855558   
299               +201144231447   
302               +201029994385   
305               +201007363696   
306               +201018176995   
307               +201551055045   
313               +201011898024   
314               +201

In [142]:
#properties_df.drop(properties_df.index,inplace=True)
properties_df = pd.DataFrame(properties_facts)
properties_df.columns = ['Reference Number', 'Property Type', 'Location', 'Area', 'Description', 'Number of Bathrooms', 'Price','Listing Date','Number of Bedrooms', 'Deveopment Project Name',  'Listing Agent Phone Number']
properties_df = properties_df.drop_duplicates()

for ind in properties_df.index:
    corrupted_address = properties_df.at[ind,'Location']
    corrupted_address = corrupted_address.replace(',', '')
    
    print(corrupted_address)
    properties_df.at[ind,'Location'] = corrupted_address

properties_df.drop(['Description'], axis = 1, inplace = True)
properties_df.to_csv(r'D:\property_finder_db\Properties - Sheet1.csv')
properties_df

null
"El Narges BuildingsCairo New Cairo City Al Narges"
"AsafraAlexandria Hay Than El Montazah"
"Blue BlueSuez Al Ain Al Sokhna"
"MarassiNorth Coast Sidi Abdel Rahman"
"Sheraton Al MatarCairo El Nozha"
"El Rehab ExtensionCairo New Cairo City Al Rehab"
"Sakeni Al Taba St.Qalyubia Obour City 3rd District"
"Al MaqsadCairo New Capital City New Capital Compounds"
"Sea ViewNorth Coast Qesm Ad Dabaah"
"Shooting Club StreetGiza Dokki"
"Fifth SquareCairo New Cairo City North Investors Area"
"Mountain View iCityCairo New Cairo City The 5th Settlement 5th Settlement Compounds"
"Bella Vento GalalaSuez Al Ain Al Sokhna"
"Smouha SquareAlexandria Hay Sharq Smouha"
"Alexandria St.Matrouh Marsa Matrouh"
"Mountain View iCityCairo New Cairo City The 5th Settlement 5th Settlement Compounds"
"Mountain View iCityCairo New Cairo City The 5th Settlement 5th Settlement Compounds"
"Lasirena Palm BeachSuez Al Ain Al Sokhna"
"MadinatyCairo"
"Sant Giyn St.Alexandria Hay Sharq Roushdy Kafr Abdo"
"Street70Cairo New

Reference Number   Property Type  \
0                               null            null   
1                             MA-126       Apartment   
2                             100021       Apartment   
3                                s45          Chalet   
4                           Lea-1123          Chalet   
5                                925       Apartment   
6                                778       Apartment   
7                                -25       Apartment   
8                            MA212MQ           Villa   
9                      SEA VIEW 125.          Chalet   
10                               331       Apartment   
11              Fifth Square-164m-ff       Apartment   
12                             P-A13          Duplex   
13                               750          Chalet   
14                            008094       Apartment   
15                      543542342545       Apartment   
16                           KR-S223       Apartment   
17                             P-A12          Duplex   
18                               734          Chalet   
19                       291022-0044       Apartment   
20                            012914       Apartment   
21                               a37       Apartment   
26                             20215       Apartment   
27                     White Sand 96          Chalet   
28                         111111111       Apartment   
29                              HS14       TwinHouse   
30                       45465563656       Apartment   
31                             P-A11       Penthouse   
32                     alaa the city       Apartment   
33                              4143          Chalet   
34                    palm hills 116       Apartment   
35                               730          Chalet   
36                             P-A10       Apartment   
37                            119380       Apartment   
38      District 5 - Town House -258           Villa   
39                        3453542542       Apartment   
40                            111666       Apartment   
41                        180m palm        Apartment   
48                        Siela Roof          Chalet   
49                        sale 165 .       Apartment   
50                              P-A9       Apartment   
51                            008093       Apartment   
52                      heba narges        Apartment   
53                        Garden 167       Apartment   
54                        4535435354       Apartment   
55                            MA-119       Apartment   
56                       N TaLahhh.,          Duplex   
57                  capital Gardens1       Apartment   
58                           sale165       Apartment   
59                   Capital Gardens       Apartment   
60                    MVICITY - 155M       Apartment   
61                           Jefaira          Chalet   
62                            345356       Apartment   
63                 C - Typical - 234       Apartment   
64                  E - Ground - 193       Apartment   
65                              P-A7           Villa   
66                                 9          Duplex   
67                                 8       Apartment   
68                              P-A6           Villa   
69                               723          Chalet   
70                     N-MView215v01          iVilla   
71                            300172       Apartment   
72                            NAS 73       Apartment   
73                              RE33       Apartment   
74                                 7          Duplex   
75                   Smeralda Bay 95          Chalet   
76                     Armonia-03.,,       Apartment   
77                             20214       Apartment   
78                              P-A5           Villa   
79                                 6       Penthouse   
80                              RE32       A

In [35]:
def get_property_info(page_soup):
    
    property_facts = []
    listing_agent_facts = []
    separator = '' #used to join lists
    
    reference_no = page_soup.find("div", {"class": "property-page__legal-list-content"})
    property_facts.append(reference_no.text)
    print("reference number = ", reference_no.text)
    
    if(page_soup.find("span", text = "Property type:")):
        ptype = page_soup.find("span", text = "Property type:")
        property_type = ptype.parent.next_sibling.text
        pptypepattern = re.compile(r'\w+') 
        pptype = separator.join(re.findall(pptypepattern, property_type))
        property_facts.append(pptype)
        print("property type: ", pptype)
    else:
        property_facts.append("null")
    
    location = "\"" #adding quotation marks to ignore any commas in the Location text 
    location += page_soup.find("div", {"class": "property-location__detail-area"}).text
    location += "\""
    property_facts.append(location)
    print( "\nlocation = ", location)
    
    if(page_soup.find("span", text = "Property size:")):
        area = page_soup.find_all("span", {"class": "property-facts__text"}) #look ahead not working for some reason
        area_pattern = re.compile(r'\b[0-9]+\s')
        area_pure = int(re.findall(area_pattern, area[1].text)[0]) #to eliminate sqm
        property_facts.append(area_pure)
        print("area: ", area_pure)
    else:
        property_facts.append("null")
    
    if(page_soup.find("div", {"class": "property-page__description"})):
        unedited_description = page_soup.find("div", {"class": "property-page__description"})
        description = "\"" #adding quotation marks to ignore any commas in the descrption text 
        description += re.sub(r'.', '', unedited_description.text, count = 11) #remove the word description from the body
        description += "\""
        property_facts.append(description)
        print( "\ndescription: ", description)
    else:
        property_facts.append("null")
    
    if(page_soup.find("span", text = "Bathrooms:")):
        bathrooms = page_soup.find("span", text = "Bathrooms:")
        no_of_bathrooms = bathrooms.parent.next_sibling.text
        property_facts.append(no_of_bathrooms)
        print( "\nnumber of bathrooms: ", no_of_bathrooms)
    else:
        property_facts.append("null")
    
    prices = page_soup.find("div", {"class": "property-price__price"})
    price_pattern = re.compile(r'[0-9]+')
    pure_price = re.findall(price_pattern, prices.text) 
    price = separator.join(pure_price) #to eliminate thousand separators
    property_facts.append(price)
    print("price: ", price)
    
    listing_date = page_soup.find_all("div", {"class": "property-page__legal-list-content"})[1].text
    listing_date = get_past_date(listing_date)
    property_facts.append(listing_date)
    print("Listing date: ", listing_date)
    
    if(page_soup.find("div", {"class": "property-payment-plan"})):
        print("here\n\n\n\n")
        down_payment = page_soup.find_all("div", {"class": "property-payment-plan__value"})[0].text
        monthly_payment = page_soup.find_all("div", {"class": "property-payment-plan__value"})[1].text
        paid_over = page_soup.find_all("div", {"class": "property-payment-plan__value"})[2].text
        #property_facts.append(down_payment)
        #property_facts.append(monthly_payment)
        #property_facts.append(paid_over)
        print("down payment: ", down_payment)
        print("monthly payment: ", monthly_payment)
        print("paid over ", paid_over)
    
    if(page_soup.find("span", text = "Bedrooms:")):
        bedrooms = page_soup.find("span", text = "Bedrooms:")
        no_of_bedrooms = bedrooms.parent.next_sibling.text
        no_of_bedrooms = no_of_bedrooms.replace(" ", "")
        no_of_bedrooms = no_of_bedrooms.replace("\t", "")
        no_of_bedrooms = no_of_bedrooms.replace("\n", "")
        property_facts.append(no_of_bedrooms)
        print("number of bedrooms = ", no_of_bedrooms)
    else:
        property_facts.append("null")
        
    if(page_soup.find("div", {"class": "property-project-details__title"})):
        dev_project_facts = []
        dev_project_name = page_soup.find("div", {"class": "property-project-details__title"}).text
        dev_project_location = page_soup.find("div", {"class": "property-project-details__location"}).text
        property_facts.append(dev_project_name)
        dev_project_facts.append(dev_project_name)
        dev_project_facts.append(dev_project_location)
        print("development project name: ", dev_project_name)
        print("development project location: ", dev_project_location)
        dev_projects_facts.append(dev_project_facts)
    else:
        property_facts.append("null")

        
        
    
    
    script_tag = page_soup.find_all("script", {"type": "application/ld+json"})[1]
    telepattern = re.compile(r'(?<=telephone":").?[0-9]+')
    listing_agent_phone = re.findall(telepattern, script_tag.text)[1]
    property_facts.append(listing_agent_phone)
    listing_agent_facts.append(listing_agent_phone)
    print("Listing agent phone number: ",listing_agent_phone)
    
    listing_agent_name = page_soup.find("h4").text
    listing_agent_facts.append(listing_agent_name)
    print("name agent", listing_agent_name)
    
    if(page_soup.find("picture", {"class": "property-agent__broker-image"}) ):
        broker_company_facts = []
        broker_company_name = page_soup.find("div", {"class": "property-agent__position-broker-name"}).text
        broker_company_name = broker_company_name.replace('\n', '')
        if(page_soup.find("a", {"class": "link link--underline"}, {"text": re.compile(r'[0-9]+(?=(\spropert(y|ies)\b))')})):
            number_of_listed_properties_tag = page_soup.find("a", {"class": "link link--underline"}, {"text": re.compile(r'[0-9]+(?=(\spropert(y|ies)\b))')})
            number_of_listed_properties = number_of_listed_properties_tag.text
            number_of_listed_properties = number_of_listed_properties.split(' ')[0]
            number_of_listed_properties = number_of_listed_properties.replace(',','')
            
            print("no listed: ", number_of_listed_properties)
            broker_company_link = "https://www.propertyfinder.eg"
            broker_company_link += number_of_listed_properties_tag['href']
            broker_response = requests.get(broker_company_link, headers=HEADERS)
            broker_soup = BeautifulSoup(broker_response.content, "html.parser")
            broker_info = broker_soup.find("div", {"class": "bio-info__details"})
            broker_address = "\""
            broker_address += broker_info.find_all("span")[1].text
            broker_address += "\""
            broker_phone = broker_soup.find("span", {"class": "button__text button__text-value button__phone-ltr button__text--is-hidden"}).text
            listing_agent_facts.append(broker_phone)
            broker_company_facts.append(broker_phone)
            broker_company_facts.append(broker_company_name)
            broker_company_facts.append(broker_address)
            broker_company_facts.append(number_of_listed_properties)
            print("broker company phone: ",  broker_phone)
            print("broker company address: ",  broker_address)
            print("broker company link: ",  broker_company_link)
            print("broker name: ", broker_company_name)
        else:
            listing_agent_facts.append("null")
            broker_company_facts.append("null")
            broker_company_facts.append("null")
            broker_company_facts.append("null")
        broker_companies_facts.append(broker_company_facts)
    
    
    
    loa = page_soup.find_all("div", {"class": "property-amenities__list"})
    for x in loa: #loa is an abbreviation for list of amenities the raw version
        amenity = []
        amenity_description = x.text
        amenity_description = amenity_description.replace('\n', '')
        amenity.append(reference_no.text)
        print("amenity refno: ",reference_no.text)
        amenity.append(amenity_description)
        print("amenity length: ", len(amenity) )
        print("amenity: ",amenity_description)
        amenities_facts.append(amenity)
    
    print("length = ", len(property_facts))
    properties_facts.append(property_facts)
    listing_agents_facts.append(listing_agent_facts)
    


In [36]:
def get_divs(p_soup):
    divs = p_soup.find_all("div", {"class": "card-list__item"})
    return divs

In [94]:
def get_page_properties(divs): 
    counter = 0
    for div in divs:
        if ((len(div.find_all("footer")) != 0) and (price_exists(div)) ):
            #above conditions used to eliminate properties with no price listed and properties that are on the page as paid promotions
            counter += 1
            print(counter)
            list_date = div.find("p", {"class": "card-footer__publish-date"})
            regexp = re.compile(r'\bhour\b|\bhours\b|\bminute\b|\bminutes\b|\bday\b|\b([2-9]|1[0-3])\b\s\bdays\b')
            if(regexp.search(list_date.text)):
                a_tag = div.find("a")
                property_link = "https://www.propertyfinder.eg"
                property_link += a_tag['href']
                print(property_link)
                page = requests.get(property_link, headers=HEADERS)
                page_soup = BeautifulSoup(page.content, "html.parser")
                if(page_soup.find("img", {"class": "property-gone__image property-gone__image--en"})): #for properties that have been delisted
                    continue
                if(property_link == r'https://www.propertyfinder.eg/en/plp/buy/chalet-for-sale-suez-al-ain-al-sokhna-la-vista-la-vista-6-3504992.html'): #edge case
                    continue
                    
                if(property_link == r'https://www.propertyfinder.eg/en/plp/buy/apartment-for-sale-cairo-ring-road-tag-sultan-3498032.html'): #edge case
                    continue
                if(property_link == r'https://www.propertyfinder.eg/en/plp/buy/apartment-for-sale-cairo-new-cairo-city-al-rehab-el-rehab-extension-3492776.html'): #edge case
                    continue
                    
                if (property_link == r'https://www.propertyfinder.eg/en/plp/buy/chalet-for-sale-suez-al-ain-al-sokhna-la-vista-la-vista-3-3492278.html'): #edge case
                    continue
                    
                if(property_link == r'https://www.propertyfinder.eg/en/plp/buy/chalet-for-sale-suez-al-ain-al-sokhna-azha-3491347.html'): #edge case
                    continue
                    
                if(property_link == r'https://www.propertyfinder.eg/en/plp/buy/chalet-for-sale-suez-al-ain-al-sokhna-la-vista-la-vista-topaz-3490254.html'): #edge case
                    continue
                    
                if(property_link == r'https://www.propertyfinder.eg/en/plp/buy/apartment-for-sale-cairo-new-cairo-city-north-investors-area-fifth-square-3487437.html'): #edge case
                    continue
                  
                if(property_link == r'https://www.propertyfinder.eg/en/plp/buy/apartment-for-sale-cairo-hay-el-maadi-maadi-cornish-el-nile-st-3481717.html'): #edge case
                    continue
                get_property_info(page_soup)
                print(len(properties_facts))
            else:
                in_date_range = False
                break
     
    update_df(devprojects_df, dev_projects_facts )
    #copy_df_to_csv(r'D:\property_finder_db\Development_projects - Sheet1.csv',   devprojects_df)
    update_df(amenities_df, amenities_facts)
    #copy_df_to_csv(r'D:\property_finder_db\amenities - Sheet1.csv',  amenities_df)
    update_df(agents_df, listing_agents_facts)
    #copy_df_to_csv(r'D:\property_finder_db\Listing_agents - Sheet1.csv',  agents_df)
    update_df(broker_df, broker_companies_facts)
    #copy_df_to_csv(r'D:\property_finder_db\Broker_companies - Sheet1.csv',  broker_df)
    update_df(properties_df, properties_facts)
    #copy_df_to_csv(r'D:\property_finder_db\Properties - Sheet1.csv',  properties_df)
    #clear_dataframes(properties_facts, amenities_facts, listing_agents_facts, broker_companies_facts, dev_projects_facts)
    

In [95]:
page_counter = 302#I update this number whenever connection is lost, if you're building the program for the first time, set it to 1
in_date_range = True
while(in_date_range):
    soup = get_soup(URL)
    my_divs = get_divs(soup)
    get_page_properties(my_divs)
    URL = increment_page(page_counter)
    page_counter += 1
    
    

1
https://www.propertyfinder.eg/en/plp/buy/apartment-for-sale-cairo-hay-el-maadi-maadi-street-9-3481732.html
reference number =  Cz200
property type:  Apartment

location =  "Street 9Cairo, Hay El Maadi, Maadi"
area:  145

description:  "شقة للبيع تمليك بشارع 9
 بأرقي موقع بالمعادي 
وتسليم فوري للجاديين 
١٤٥ متر عبارة عن ٣غرفة نوم مقفولة 
ريسبشن واسع قطعتين 
حمام،، ومطبخ 
 الشقه ١٤٥م تشطيب الترا سوبر لوكس
 شارع ٩ الرئيسي  المعادي
 الدور الثالث اسانسير جراج أمن وحراسه مرخصه شهر عقاري... 2مليون 
قابل للتفاوض البسيط 
التواصل /+2+201099222621
Apartment for sale, ownership, on Street 9, in the finest location in Maadi, and immediate delivery to the serious, 145 meters, consisting of 3 bedrooms, closed, spacious reception, two pieces, bathroom, and kitchen. For simple negotiation, contact / +2+201099222621"

number of bathrooms:  1
price:  2000000
Listing date:  2022-10-16
number of bedrooms =  3+Maid
Listing agent phone number:  +201099222621
name agent قرطاج العقارية
no listed:  46
broker 

C:\Users\hamza\AppData\Local\Temp\ipykernel_4240\2919434248.py:2: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(pd.DataFrame(x_facts))


1
https://www.propertyfinder.eg/en/plp/buy/apartment-for-sale-cairo-hay-el-maadi-maadi-street-9-3481732.html
reference number =  Cz200
property type:  Apartment

location =  "Street 9Cairo, Hay El Maadi, Maadi"
area:  145

description:  "شقة للبيع تمليك بشارع 9
 بأرقي موقع بالمعادي 
وتسليم فوري للجاديين 
١٤٥ متر عبارة عن ٣غرفة نوم مقفولة 
ريسبشن واسع قطعتين 
حمام،، ومطبخ 
 الشقه ١٤٥م تشطيب الترا سوبر لوكس
 شارع ٩ الرئيسي  المعادي
 الدور الثالث اسانسير جراج أمن وحراسه مرخصه شهر عقاري... 2مليون 
قابل للتفاوض البسيط 
التواصل /+2+201099222621
Apartment for sale, ownership, on Street 9, in the finest location in Maadi, and immediate delivery to the serious, 145 meters, consisting of 3 bedrooms, closed, spacious reception, two pieces, bathroom, and kitchen. For simple negotiation, contact / +2+201099222621"

number of bathrooms:  1
price:  2000000
Listing date:  2022-10-16
number of bedrooms =  3+Maid
Listing agent phone number:  +201099222621
name agent قرطاج العقارية
no listed:  46
broker 

KeyboardInterrupt: 

In [88]:
print(page_counter) #to know the page number where the

309


In [112]:
from faker import Faker

In [115]:
faker_obj = Faker()
gender = 'M'
lst = []
for i in range(1000): # code I found online to generate fake user info
    male_profile = faker_obj.simple_profile(sex=gender)
    print("Male profile generated is as follows:\n", male_profile)
    lst.append(male_profile)
    gender = 'F'
    male_profile = faker_obj.simple_profile(sex=gender)
    print("Female profile generated is as follows:\n", male_profile)
    lst.append(male_profile)
    

Male profile generated is as follows:
 {'username': 'vazquezsteve', 'name': 'Adam Blake', 'sex': 'M', 'address': '79066 Leslie Union\nSouth Troyland, NV 35617', 'mail': 'ralexander@gmail.com', 'birthdate': datetime.date(1998, 1, 20)}
Female profile generated is as follows:
 {'username': 'imunoz', 'name': 'Theresa Long', 'sex': 'F', 'address': '13311 Jackson Gardens\nSouth Douglasside, SD 58129', 'mail': 'ywagner@hotmail.com', 'birthdate': datetime.date(1968, 4, 15)}
Male profile generated is as follows:
 {'username': 'mendozaaaron', 'name': 'Pamela Green', 'sex': 'F', 'address': 'Unit 3030 Box 7361\nDPO AA 05347', 'mail': 'phyllis88@hotmail.com', 'birthdate': datetime.date(2019, 7, 19)}
Female profile generated is as follows:
 {'username': 'candicerobinson', 'name': 'Shelby Morrison', 'sex': 'F', 'address': '3785 Martin Camp Apt. 508\nPort Bradleyland, WI 24947', 'mail': 'dtate@hotmail.com', 'birthdate': datetime.date(2017, 11, 1)}
Male profile generated is as follows:
 {'username': 'r

In [122]:
user_df.drop(user_df.index,inplace=True)

In [124]:
user_df = pd.DataFrame(lst)
user_df.drop(['name', 'address'], axis = 1, inplace = True)
user_df = user_df.drop_duplicates()
user_df.to_csv(r'D:\property_finder_db\Users - Sheet1.csv')
user_df

username sex                            mail   birthdate
0            vazquezsteve   M            ralexander@gmail.com  1998-01-20
1                  imunoz   F             ywagner@hotmail.com  1968-04-15
2            mendozaaaron   F           phyllis88@hotmail.com  2019-07-19
3         candicerobinson   F               dtate@hotmail.com  2017-11-01
4               rosegomez   F              alec15@hotmail.com  1933-01-14
5                 kmartin   F                blewis@gmail.com  1992-11-15
6               colleen94   F          whitemichael@yahoo.com  1967-08-13
7               charles32   F           barryrachel@gmail.com  1910-08-06
8               sherrylee   F          jonesjason@hotmail.com  1986-02-19
9                  kdavis   F              brooke33@yahoo.com  1992-03-17
10            martinshawn   F              tbrown@hotmail.com  1954-09-11
11               joseph16   F        williamssean@hotmail.com  1953-03-21
12                shawn55   F             deborah71@gmail.com  1974-05-21
13                  hleon   F            duranjames@yahoo.com  1907-04-10
14                 dmason   F                  dfox@gmail.com  2001-11-19
15           michaelolson   F       campbelldarlene@yahoo.com  1938-06-25
16            frederick10   F             brianlong@gmail.com  2006-03-25
17           lewisnatasha   F               arice@hotmail.com  1985-09-02
18               rperkins   F              edward93@gmail.com  1986-07-30
19          annafernandez   F            foxmaxwell@gmail.com  1921-09-01
20         williamhouston   F         garrisonjason@yahoo.com  1976-11-26
21                jgarcia   F                lbrown@gmail.com  1971-04-25
22                  ldunn   F       jonathanwallace@gmail.com  1951-10-04
23              barbara01   F              egates@hotmail.com  1942-08-25
24                 wsmith   F       gonzalezgregory@gmail.com  2014-10-30
25                  vneal   F          sharpdonna@hotmail.com  1974-11-22
26                donna49   F             chrishall@yahoo.com  2003-08-13
27              patelbeth   F              kfritz@hotmail.com  1973-01-13
28           clarklindsey   F          michellebell@gmail.com  1980-09-17
29              omartinez   F        hoffmandavid@hotmail.com  1934-08-07
30             millertodd   F         petersonapril@gmail.com  1963-12-31
31           grantjohnson   F        hannahdelacruz@gmail.com  1913-08-16
32           geoffreykemp   F            donald10@hotmail.com  1949-02-20
33                cmurray   F         michaelnorton@gmail.com  1965-01-25
34       buckleychristina   F         spearswhitney@gmail.com  1969-02-13
35              ecampbell   F             kristen18@yahoo.com  1936-01-29
36             xdonaldson   F                hflynn@yahoo.com  1939-01-14
37            casemonique   F              ybaldwin@yahoo.com  1945-05-03
38          andrewsanchez   F        khanmadeline@hotmail.com  1919-04-30
39           robertcastro   F   ericksonelizabeth@hotmail.com  1986-11-11
40                 mary64   F             jamie40@hotmail.com  1967-12-10
41               zwilkins   F             anthony82@yahoo.com  1988-05-06
42               jeremy92   F              rherrera@gmail.com  1957-02-09
43                sarah82   F              lisa80@hotmail.com  1943-03-18
44           monicagarcia   F              bkennedy@yahoo.com  1916-06-11
45           wilsonregina   F           cindygarcia@yahoo.com  1909-07-18
46                 hlopez   F             tranjason@yahoo.com  1949-07-06
47               morgan53   F              adam59@hotmail.com  1994-02-08
48                snelson   F         nicholsonbrad@gmail.com  1999-01-28
49              clinton65   F              robert96@gmail.com  1986-05-07
50             morrisjill   F               julie03@gmail.com  1954-03-16
51                 marc65   F             laura37@hotmail.com  1964-11-03
52          phillipslarry   F          lawrence61@hotmail.com  1948-05-17
53          daniellem

In [146]:
import random

In [252]:
ref_agent = random.choice(properties_facts)
print(ref_agent[0], ref_agent[10])
print(random.choice(lst)['name'])
print(random.randint(0,10))
fake = Faker()
print(fake.date_between_dates(date_start=datetime.date(2015,1,1), date_end=datetime.date(2021,12,31)))

ZA 2772 +201013944435
Samantha Francis
10
2019-04-18


In [256]:
saves_df.drop(saves_df.index,inplace=True)

In [266]:
saves_fact = []
for i in range(500):
    ref_agent = random.choice(properties_facts)
    ref_agent_2 = []
    ref_agent_2.append(random.choice(lst)['name'])
    ref_agent_2.append(ref_agent[0])
    
    saves_fact.append(ref_agent_2)
    
    
    
saves_df = pd.DataFrame(saves_fact)
saves_df.to_csv(r'D:\property_finder_db\Saves - Sheet1.csv')
saves_df

0                               1
0            Melanie Coffey       للبيع شقه تمليك الياسمين 
1             Kristin Baker                       235 م هبة
2              Kathy Martin                             203
3                 Stacy Fox                         nour 99
4             Sylvia Harris  Apartment IL Bosco New Capital
5           Vanessa Johnson                       YE-ANNTRI
6          Kimberly Johnson                             A33
7              Briana Lloyd                          204288
8              Denise Doyle                       25-10 #10
9            Amanda Hoffman                          ZT 327
10             Phyllis Ryan                            9060
11            Beverly Moses                      telal 96..
12            Carmen Suarez                          119371
13     Mrs. Katrina Griffin                         ZA 2749
14             Donna Vargas                        سيفورا 2
15                Kim Clark                   rabeh-3545677
16               Jenny Dunn                           s1412
17         Christina Bowman                            DD11
18             Katie Nelson                       25-10 #25
19          Natalie Hawkins                       333218633
20           Shelley Harris                        AE60AE24
21         Christine Bailey                           AZ-11
22            Katelyn Short                         CP.NM.2
23             Judith Kelly                        nihal 82
24     Christina Villanueva                    F- patio oro
25               Tara Olson                             271
26            Alexis Lowery                               D
27             Melissa Hall                     RM midtown\
28           Kristen Fields                           s1412
29         Ashley Hernandez              Apartment155 25/10
30              Erica Reyes                             146
31              Tracy Smith                          o1w130
32              Megan Reyes                            A214
33             Pamela Evans                        LVR-0022
34           Jackie Vaughan                          SAV160
35            Sharon Guzman                              33
36       Christine Mitchell                          AD 313
37       Elizabeth Crawford            mustafa farag louts 
38         Stephanie Reeves                  IL BOSCO 150 M
39        Tricia Villarreal                         dina 89
40              Regina King                             197
41            Andrea Rogers                             96m
42         Jennifer Cameron                      PFAA242-01
43          Jessica Allison                              03
44            Monica Santos                         ZA 2777
45            Shannon Ellis                            96m 
46              Janice Paul                            TC51
47          Monica Peterson                        PF0536-3
48        Kimberly Franklin                         Sand013
49           Lindsey Mccann                      عمر  احمد 
50                Amy Young                       27-10 #37
51           Heather Rivera                         ZA 2765
52            Brooke Butler                         0080288
53           Carla Townsend                           mpp22
54            Rachel Flores                             734
55            Allison Moore                         Sand017
56            Amy Henderson                         1113337
57          Katherine Black                        R 165 CS
58           Deborah Nguyen                      blumar-n-p
59                Lisa Reed                    MARASEM 136M
60           Brittany Clark                            9848
61                Jodi Hall                          306789
62           Sarah Thompson                      5435353577
63           Elaine Sanchez                            RE31
64          Abigail Holland                          z96 ho
65        Mrs. Sydney Smith                         Prim043
66    

In [262]:
contacts_facts = []
for i in range(200):
    ref_agent = random.choice(properties_facts)
    ref_agent_2 = []
    ref_agent_2.append(random.choice(lst)['name'])
    ref_agent_2.append(ref_agent[0])
    ref_agent_2.append(ref_agent[10])
    
    contacts_facts.append(ref_agent_2)
    
    
contacts_df = pd.DataFrame(contacts_facts)
contacts_df.to_csv(r'D:\property_finder_db\Contacts - Sheet1.csv')
contacts_df

0                               1  \
0       Mrs. Heather Holmes                             989   
1             Amanda Wright                         Sara 12   
2              Carla Martin              flagsquare-3546885   
3                Mary Brown                             381   
4              Jamie Levine                           AEC-2   
5             Rachel Dawson                            Y 10   
6               Lori Sutton                            0317   
7           Felicia Ramirez                             412   
8          Adrienne Fleming                            ms78   
9            Stacie Higgins                         R212 S2   
10             Maria Garcia                       24-10 #73   
11          Courtney Arnold                      3546354634   
12           Julie Lawrence                        (RK_395)   
13            Cheyenne Wang                  pointmark-9851   
14                Dana Khan                            2229   
15          Teresa Morrison                           20183   
16              Paula Smith                         2210223   
17              Tina Willis                       H.baro 91   
18           Erin Bauer PhD                               5   
19           Mrs. Ruth Rice               ashraf icity165..   
20            Amanda Miller                            6183   
21              Jean Dudley                        villette   
22          Candace Randall                          PF0520   
23         Candice Gonzalez                         ZA 2775   
24        Jennifer Anderson                             -21   
25          Julie Gillespie             Mountain v sukhna h   
26          Amy Baldwin DDS                             371   
27          Samantha Parker                         MZ.beta   
28             Michele Ward                         an-6-33   
29          Rhonda Richards                            0288   
30              Sue Alvarez              Trio Compound -$$%   
31             Pamela Kline                     abdelqawy12   
32           Sarah Thompson                             147   
33         Michelle Watkins                    es-Al Maqsad   
34            Natalie Reese       اي فيلا سكاي ماونتن فيو 1   
35            Sherry Campos                rootsdev-3562211   
36            Katelyn Short                             204   
37      Ms. Maria Jones DVM                     43543574354   
38             Kara Simpson                         NA-9292   
39          April Middleton                        PF0537-1   
40         Stephanie Baxter                          A.A224   
41           Julie Lawrence                       24-10 #65   
42            Alexis Cooper                           00062   
43            Samantha Diaz                     201022-0001   
44                 Tina Roy                         Sand041   
45   Mrs. Melissa Allen DDS                     palm hills1   
46             Jessica Paul                         i181925   
47            Leslie Turner                             357   
48       Jasmine Hutchinson                             -21   
49   Mrs. Theresa Stevenson                       M/AZB 344   
50                Jill Hale                       bavaria 1   
51             Jaime Zuniga                         TS30018   
52          Lisa Gregory MD                           BR502   
53                Mary Wang                        Badya.13   
54          Victoria Norman                  jayd 170m shhh   
55            Jessica Sloan            270 متر تقسيط 12 شهر   
56           Pamela Gregory                  S penthouse 2    
57          Mrs. Erin Young                            8532   
58      Miss Angela Bell MD                         CP.NM.8   
59            Andrea Barker                             i22   
60            Ashlee Davila                             i41   
61             Brandy Davis                         is 2568   
62                Kim Clark                          1193

In [264]:
reviews_facts = []
for i in range(200):
    ref_agent = random.choice(properties_facts)
    ref_agent_2 = []
    ref_agent_2.append(random.choice(lst)['name'])
    ref_agent_2.append(ref_agent[10])
    ref_agent_2.append(fake.date_between_dates(date_start=datetime.date(2015,1,1), date_end=datetime.date(2021,12,31)))
    ref_agent_2.append(random.randint(0,10))
    reviews_facts.append(ref_agent_2)
reviews_df = pd.DataFrame(reviews_facts)
reviews_df.to_csv(r'D:\property_finder_db\Reviews - Sheet1.csv')
reviews_df
    

0                   1           2   3
0                 Kim Mccoy        +20221257322  2015-08-12   7
1             Leslie Turner       +201119979281  2020-07-02   6
2             Amber Estrada       +201050800596  2017-07-24   1
3          Jennifer Kennedy       +201111675397  2017-12-24   2
4            Kimberly Baker       +201111778807  2018-09-16   1
5               Carol White       +201022000981  2016-07-14   8
6            Brooke Simpson       +201033653009  2015-07-09   6
7               Misty Green       +201092445451  2019-04-14  10
8               Katelyn Fox        +20221256990  2018-12-22   7
9             Kaitlyn Jones       +201099655581  2015-05-03   7
10            Miranda Adams       +201060619779  2020-01-28   4
11            Kaitlyn Brown       +201226600677  2015-11-10   0
12          Jessica Allison        +20221256907  2020-12-12   2
13               Erin Green       +201207411224  2018-04-30   1
14            Andrea Taylor       +201016333687  2016-09-11   9
15          Lindsay Edwards       +201033337707  2017-03-19   4
16       Holly Johnston DDS        +20221257151  2018-01-18   2
17            Michele Evans       +201017541738  2021-03-22   0
18               Gina Scott       +201119979281  2018-12-31  10
19              Amanda Diaz       +201211600832  2019-11-06  10
20            Mary Sandoval       +201061815207  2016-06-10   0
21            Dominique Cox       +201289225412  2020-12-07   0
22             Mary Stewart       +201112220853  2020-09-20  10
23            Megan Sanders        +20221256990  2016-09-23   9
24             Julia Santos  +20106300047316209  2021-07-12   3
25             Debbie Yoder       +201028089585  2015-06-30   5
26              Debra Brown       +201234555575  2021-09-16   1
27         Wendy Pennington       +201015757708  2020-10-01   7
28           Katrina Sutton        +20221257322  2016-05-06   9
29               Erica Pena       +201022228857  2016-05-18   8
30             Sheila Rivas       +201210003824  2017-11-29   8
31            Michele Mills       +201008832291  2019-07-04   7
32            Nancy Hopkins       +201096041789  2017-02-17   7
33              Grace Joyce       +201011523636  2015-12-31   1
34             Hannah Miles       +201009002282  2020-01-29   4
35            Raven Sanchez       +201033337707  2018-10-06   0
36           Lori Macdonald       +201033337707  2020-08-29   2
37              Debra Moore        +20221257381  2016-06-27   3
38            Lorraine Long       +201119979281  2015-02-11   1
39           Kathleen Mejia       +201020844778  2019-01-05   3
40                Erika Fry       +201067257296  2020-10-17   1
41         Patricia Barnett       +201102989131  2018-06-27   2
42         Amanda Wilkinson       +201211769112  2019-11-04   6
43             Linda Bishop       +201140300403  2019-04-30   3
44            Jennifer Hunt       +201200100885  2017-08-25   8
45          Judith Cummings       +201050863940  2020-07-09   3
46         Wendy Pennington        +20221257491  2018-01-14   7
47              Robin Perez       +201050990178  2018-04-22   8
48         Kristin Chandler       +201009366996  2020-08-05   4
49           Angela Meadows        +20221257363  2017-02-18   8
50            Jennifer Hunt       +201119979281  2016-04-21   4
51           Andrea Schmidt       +201022442560  2019-10-08   5
52            Michele Jones       +201005955533  2020-11-16   4
53           Faith Gonzalez       +201009000782  2015-02-08   3
54             Jamie Nelson       +201283123332  2018-11-23   4
55             Sandra Clark       +201050404653  2021-04-22   8
56          Cheryl Richmond       +201011409577  2015-09-03   9
57                Dawn Todd       +201015757708  2017-11-09   1
58             Sandra Smith       +201001414045  2021-04-15   6
59             Denise Doyle        +20221257413  2015-05-22   8
60          Dana Richardson       +201008892862  2019-08-19   2
61        Michelle Schwartz       +201098564643  2017-05-2